# Simple Tree

---
## Experimental Setup

### Libraries & Settings

In [1]:
import os              # General OS commands
import numpy as np     # NumPy
import pandas as pd    # Python Data Analysis Library
import zipfile         # Compress/decompress ZIP files
import sqlite3         # SQLite3 Database Driver
import re              # Regular Expressions

In [2]:
import pydotplus
from IPython.display import Image
from sklearn import metrics, tree

In [3]:
# Never truncate columns, display all the data
from IPython.display import display, HTML
pd.set_option('display.max_colwidth', -1)

# Display floating-point numbers with 4 decimals in `pandas.DataFrame`
pd.options.display.float_format = '{:,.4f}'.format

import matplotlib.pyplot as plt
# Display MatPlotLib stuff inline
%matplotlib inline

### Database

In [4]:
zip_filename = "../data/ee-insee-2015_custom-sqlite.zip"
eedb = zip_filename.replace("-sqlite.zip", ".sqlite")

if not os.path.exists(eedb):
    with zipfile.ZipFile(zip_filename) as zip_file:
        zip_file.extractall("../data/")

In [5]:
with sqlite3.connect(eedb) as con:
    query = "SELECT * FROM eec15_custom"
    eec15 = pd.read_sql_query(query, con)

In [6]:
# Create a ("female" x "enfant") interaction variable
bool_ = eec15[["enfants_", "female_"]].astype(bool)
eec15["female_enfants_"] = (bool_.enfants_ & bool_.female_).astype(int)

# Drop data we don't need
eec15 = eec15[eec15.age60_ == 0]
eec15 = eec15.drop("age60_", 1)

---
## Simple Tree

In [7]:
# Build a list of parameters to include in the model, using regex
# https://www.datarobot.com/blog/multiple-regression-using-statsmodels/
filters = {
    "age": "^age[0-9]{2}_$",
    "diploma": "^dip[0-9]{2}_$",
    "etranger": "^etranger_$",
    "domtom": "^domtom_$",
#     "trim": "^trim$",
    "female": "^female_$",
    "enfants": "^enfants_$",
#     "female_enfants": "^female_enfants_$",
    "region": "^region[1-2]_$"
}
params = {k: sorted([x for x in eec15.columns if re.match(r, x)]) for (k, r) in filters.items()}

# Avoid the dummy variable trap
params = {k: (v if len(v) == 1 else v[:-1]) for (k, v) in params.items()}
params["region"] += ["region2_"]

In [8]:
trims = ["t{}".format(x) for x in sorted(eec15["trim"].unique())]
eec15_ = {t: eec15[eec15.trim == int(t[1])] for t in trims}
X = {t: eec15_[t][sum(params.values(), [])] for t in eec15_}
y = {t: eec15_[t]["actop_"] for t in eec15_}

### Train the model using `trim=1` data

In [9]:
# Create & fit the tree
simple_tree_sk = tree.DecisionTreeClassifier(max_depth=9, random_state=0).fit(X["t1"], y["t1"])

#X_combined = np.vstack((X_, X_test2))
#Y_combined = np.hstack((Y_, y_test2))

In [10]:
# Check the accuracy of the model on the training set
print "Accuracy: {}".format(simple_tree_sk.score(X["t1"], y["t1"]))

Accuracy: 0.766028721272


In [11]:
# Create a graphical representation of the tree
dot_data = tree.export_graphviz(
    simple_tree_sk,
    out_file=None,
    feature_names=X["t1"].columns,
    filled=True,
    rounded=True,
    special_characters=True
)
graph = pydotplus.graph_from_dot_data(dot_data)

# Save the graph to a .png file
png_file = "../img/simple_tree.png"
graph.write_png(png_file)

True

In [12]:
# Load and display the graph from file
Image(png_file)

### Apply the model to test data (`trim=2/3/4`)

In [13]:
# Check the accuracy of the model on the training & test sets

for t in trims:
#     predicted = simple_tree_sk.predict_proba(X[t]).T[1]
#     predicted = np.where(predicted < 0.5, 0, 1)
    predicted = simple_tree_sk.predict(X[t])
    print "Accuracy ({}): {}".format(t, metrics.accuracy_score(y[t], predicted))

# Note: the two methods for computing `predicted` are equivalent (THRESHOLD = 0.5)

Accuracy (t1): 0.766028721272
Accuracy (t2): 0.772443785658
Accuracy (t3): 0.764065362138
Accuracy (t4): 0.767240767298


---
## Marginal Effects

In [14]:
marginal_effects = pd.DataFrame()

### By modifying the dataset ("passage de tout le monde en licence")

In [15]:
brute_force = pd.Series()
for category in filters:
    for pivot in params[category]:
        non_pivots = [x for x in params[category] if x != pivot]
        
        X_one = X["t1"].copy() 
        X_one[non_pivots] = 0
        X_one[pivot] = 1
        
        proba_one = simple_tree_sk.predict_proba(X_one).T[1].mean()
        proba_t1 = simple_tree_sk.predict_proba(X["t1"]).T[1].mean()
        brute_force[pivot] = proba_one - proba_t1

In [16]:
marginal_effects["brute_force"] = brute_force
marginal_effects.transpose()

etranger_  age15_  age30_  age40_  dip10_  dip11_  dip30_  \
brute_force 0.1343     0.1741  -0.1044 -0.1152 -0.1657 -0.2200 0.0806    

             dip31_  dip33_  dip41_  dip42_  dip50_  dip60_  dip70_  female_  \
brute_force -0.1447 -0.0003 0.0781  -0.0860 -0.0110 0.1194  0.0776  0.0344     

             enfants_  region1_  region2_  domtom_  
brute_force -0.0754   0.0002    0.0009    0.1037

**TODO:** figure out what Bastien was trying to do with `X_3`

---
## Most important parameters
_ranked by **Gini importance**_ ("les plus clivantes")

In [17]:
gini = pd.DataFrame(simple_tree_sk.feature_importances_, index=X["t1"].columns, columns=['gini'])
gini.sort_values(by='gini', ascending=False).transpose()

age15_  dip60_  domtom_  etranger_  dip41_  dip10_  enfants_  female_  \
gini 0.5171  0.1131  0.0566   0.0484     0.0441  0.0347  0.0335    0.0312     

      dip50_  dip11_  dip31_  dip42_  dip33_  age30_  age40_  region1_  \
gini 0.0273  0.0255  0.0247  0.0245  0.0088  0.0040  0.0026  0.0020      

      region2_  dip70_  dip30_  
gini 0.0019    0.0001  0.0000